In [65]:
import pickle
import pandas as pd
import networkx as nx
from bertopic import BERTopic
from tqdm import tqdm
import matplotlib.pyplot as plt
from matplotlib_venn import venn2
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
import umap.umap_ as umap
import string
import gensim
from gensim.parsing.preprocessing import remove_stopwords
from gensim.utils import simple_preprocess
import pyLDAvis.gensim_models
import plotly.express as px
from nltk.stem import WordNetLemmatizer
import nltk
import itertools
nltk.download('wordnet')


[nltk_data] Downloading package wordnet to
[nltk_data]     /user/machaves/home/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

# Topic modeling

The tweets' data contains topic ID information which is a code that identifies the topic of the tweet.
However we do not have information about the how these IDs map to a topic name.
As it is shown below, the ```statistics.json``` file has information only of a couple of them.
Therefore, we use different topic modeling methods to filter the components according to the topics that interest us.

In the next cell we see that only 9 out of 126 topic IDs have a name/description.

In [2]:
# Load topic ids and description
df_topics_names = pd.read_json("datasets/statistics.json")[['topic_id', 'title']]

print('Topic ids with description')
print(df_topics_names)


# Load df_tweets
df_tweets = pickle.load(open("results/df_tweets.pkl", "rb"))

print('All topic IDs')
df_tweets[['new_id', 'topics']] \
    .explode(['topics']) \
    .reset_index(drop=True) \
    .rename(columns={"topics": "topic_id"}) \
    .groupby('topic_id').min() \
    .reset_index() \
    .merge(df_topics_names, on = 'topic_id', how = 'left')

Topic ids with description
  topic_id                                 title
0   2002p1                azithromycin and covid
1   2013p2                 invermectin and covid
2   2046p1                      bleach and covid
3   2081p2                       moderna vaccine
4   2082p2                   astrazeneca vaccine
5   2101p1                          5g and covid
6   2102p1                   covid is artificial
7   2104p2  blood types and covid susceptibility
8   2126p1       army mobilizations during covid
9   2129p2                        h1n1 and covid
All topic IDs


topic_id  new_id                   title
0     2001p1  100034                     NaN
1     2002p1  100034  azithromycin and covid
2     2002p2  100727                     NaN
3     2003p1  100338                     NaN
4     2003p2  101991                     NaN
..       ...     ...                     ...
121   2131p2  110074                     NaN
122   2132p1   12728                     NaN
123   2132p2   10000                     NaN
124   2133p1  114579                     NaN
125   2133p2  112543                     NaN

[126 rows x 3 columns]

## Hashtags by topic

Using the hashtags of each topic does not help in our topic selection because some topic codes are not associated to any hashtags. 

In [75]:
# Hashtags by topic
df_tweets[['hashtags', 'topics']] \
    .explode(['topics']).explode('hashtags') \
    .groupby('topics')['hashtags'].agg(lambda x: set(x)) \
    .reset_index() \
    .to_csv('results/hashtags_by_topic.csv')

## BERTopic

We ask BERTopic to extract 126 because there are 126 topic IDs. 
On other experiments, where BERTopic chose the number of clusters, we ended up with more that 1000 topic clusters. 

Due to the stochastic nature of UMAP, the results from BERTopic might differ on different runs. 
Setting a seed for reproducibility is not trivial since the way to do it is by setting a random_state in custom embeddings to prevent any stochastic behavior.
Therefore, to obtain better results, we do not use the custom embeddings.  

Create a list of text to pass to BERTopic

In [3]:
# Load df_tweets
df_tweets = pickle.load(open("results/df_tweets.pkl", "rb"))

# Concatenate tweets by component
df_components_text = df_tweets[['text', 'component_id']] \
    .groupby('component_id')['text'].apply(','.join).reset_index()

# Remove words starting with '@' from the text column
df_components_text['text'] = df_components_text['text'].str.replace(r'@\w+\s?', '', regex=True)

# List of strings
docs = list(df_components_text['text'])
docs[2]

'Covid19 pandemic could be stopped but greed, power and profits take precedence over saving lives. It appears the scientists and doctors are scavenging for research funding and hence the fervent support for vaccines without long term data on side effects.,Covid19 pandemic could be stopped but greed, power and profits take precedence over saving lives. It appears the scientists and doctors are scavenging for research funding and hence the fervent support for vaccines without long term data on side effects.,The Covid-19 pandemic could be stopped but greed, power and profits take precedence over saving lives...🤔,The Covid-19 pandemic could be stopped but greed, power and profits take precedence over saving lives.,The Covid-19 pandemic could be stopped but greed, power and profits take precedence over saving lives.,The Covid-19 pandemic could be stopped but greed, power and profits take precedence over saving lives.,The Covid-19 pandemic could be stopped but greed, power and profits take p

In [30]:
# Use BERTopic to identify clusters of components with the same topic.
# It's better to run this on a GPU, otherwise it is quite time consuming.
# The enviroment where the model was store has to be same as the one in which you load it.
# topic_model = BERTopic(nr_topics=126)
# topics, probabilities = topic_model.fit_transform(docs)

# Save results from model 
# topic_model.save("results/topic_model")
topic_model = BERTopic.load("results/topic_model")

# pickle.dump((topics, probabilities), open("results/topics_probabilities.pkl", "wb"))
topics, probabilities = pickle.load(open("results/topics_probabilities.pkl", "rb"))

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Topic -1 refers to all outliers and should typically be ignored. But we notice that many of the components fall into that category. Therefore BERTopic might not be the best way to continue our characterization. 

In [31]:
topic_model.get_topic_info()

Topic  Count                                            Name   
0       -1  66953                                -1_the_to_and_of  \
1        0  13851              0_ivermectin_for_covid19_treatment   
2        1  11550              1_moderna_vaccine_pfizer_effective   
3        2   8127  2_thread_azithromycin_hydroxychloroquine_tweet   
4        3   5933                           3_trump_bleach_he_his   
..     ...    ...                                             ...   
121    120     11                120_co2_ppm_covidco2_ventilation   
122    121     11                    121_beer_martini_vodka_glass   
123    122     11                   122_brees_drew_relief_opinion   
124    123     11                      123_florida_nvm_stoopid_js   
125    124     10                     124_tunnel_end_light_graphs   

                                        Representation   
0       [the, to, and, of, is, in, for, it, that, you]  \
1    [ivermectin, for, covid19, treatment, of, the,...   
2    [moderna, vaccine, pfizer, effective, vaccines...   
3    [thread, azithromycin, hydroxychloroquine, twe...   
4    [trump, bleach, he, his, coronavirus, presiden...   
..                                                 ...   
121  [co2, ppm, covidco2, ventilation, classroom, w...   
122  [beer, martini, vodka, glass, oz, shaker, cock...   
123  [brees, drew, relief, opinion, donated, anthem...   
124  [florida, nvm, stoopid, js, foolishness, man, ...   
125  [tunnel, end, light, graphs, salam, excellentl...   

                                   Representative_Docs  
0    [And it is never limited... governments may ba...  
1    [So, you know what the doctors did but they do...  
2    [Moderna COVID-19 vaccine nearly 95 percent ef...  
3    [COVID ICU Drs held a press conference on how ...  
4    [White House Press should ask about this,I wis...  
..                                                 ...  
121  [#COVIDCO2 My second cinema visit with a CO2 m...  
122  [I'll enjoy a modelo, official beer of the UFC...  
123  [I wonder is ed reed thinks is a sucka for don...  
124  [Florida is all I needed to see, Florida is re...  
125  [The World Will Seen a Light at the End of the...  

[126 rows x 5 columns]

In [37]:
topic_model.visualize_topics()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'customdata': array([[0, 'ivermectin | for | covid19 | treatment | of', 13851],
                                   [1, 'moderna | vaccine | pfizer | effective | vaccines', 11550],
                                   [2,
                                    'thread | azithromycin | hydroxychloroquine | tweet | coronavirusexpert',
                                    8127],
                                   ...,
                                   [122, 'brees | drew | relief | opinion | donated', 11],
                                   [123, 'florida | nvm | stoopid | js | foolishness', 11],
                                   [124, 'tunnel | end | light | graphs | salam', 10]], dtype=object),
              'hovertemplate': '<b>Topic %{customdata[0]}</b><br>%{customdata[1]}<br>Size: %{customdata[2]}',
              'legendgroup': '',
              'marker': {'color': '#B0BEC5',
                         'line': {'color': 'DarkSlateGrey', 'width': 2},
                         'size': array([13851, 11550,  8127,  5933,  4097,  1329,  1252,  1117,  1015,   986,
                                          796,   703,   624,   606,   564,   522,   490,   487,   426,   425,
                                          388,   354,   313,   239,   219,   213,   208,   207,   204,   193,
                                          188,   172,   143,   141,   122,   116,   107,    97,    97,    92,
                                           88,    83,    82,    81,    78,    78,    66,    63,    62,    62,
                                           58,    58,    54,    54,    51,    50,    48,    48,    44,    41,
                                           39,    38,    34,    32,    32,    32,    31,    30,    30,    29,
                                           28,    28,    28,    28,    26,    25,    25,    25,    23,    23,
                                           23,    22,    21,    20,    20,    18,    17,    17,    17,    17,
                                           16,    16,    15,    15,    14,    14,    14,    14,    14,    14,
                                           14,    14,    14,    14,    13,    13,    13,    13,    13,    13,
                                           12,    12,    12,    12,    12,    11,    11,    11,    11,    11,
                                           11,    11,    11,    11,    10]),
                         'sizemode': 'area',
                         'sizeref': 8.656875,
                         'symbol': 'circle'},
              'mode': 'markers',
              'name': '',
              'orientation': 'v',
              'showlegend': False,
              'type': 'scatter',
              'x': array([14.2641945 ,  0.6762166 , 14.684164  ,  3.8436172 ,  1.2575213 ,
                           1.3049802 ,  5.165656  ,  5.5345097 ,  5.387484  ,  5.2506933 ,
                           5.442278  ,  0.10852564,  0.5430783 , 13.801866  ,  0.1531165 ,
                           0.63501036, 13.628061  ,  4.285465  ,  1.1508757 , -3.2252061 ,
                           5.382465  , 10.5798025 ,  1.3142223 ,  5.122989  , 10.535512  ,
                           0.56919384,  5.479236  ,  1.0762395 ,  0.02221011, -9.178127  ,
                           5.002698  ,  3.8036633 ,  1.7099888 , -5.341526  ,  6.055238  ,
                           4.286773  , 10.739641  , -9.487471  ,  1.7779423 ,  4.530765  ,
                           6.1318665 , -9.377286  ,  4.1472287 ,  6.02063   , 15.043933  ,
                          13.946831  ,  5.6566043 ,  0.904045  ,  1.2732145 , -3.2210097 ,
                           0.53572893,  5.6723585 , 10.588522  ,  4.122254  ,  4.5507226 ,
                          -9.17797   ,  4.225253  ,  0.27459884,  0.2981371 , 14.372009  ,
                           3.7224753 ,  1.1605096 ,  3.9310844 , -3.2293146 , -5.3415465 ,
                          14.584076  , 13.665789  , 14.374615  , 10.482263  ,  1.4101299 ,
                          -3.271719  ,  5.406356 

## LDA

We try using LDA with different number of topics, in all cases we find overlaps of the words associated to each topic which suggests that the model is not discening correctly between different groups of topics.    


Useful links
> On coherence metrics: https://www.baeldung.com/cs/topic-modeling-coherence-score

> On LDA implementation and inner-workings: https://towardsdatascience.com/nlp-extracting-the-main-topics-from-your-dataset-using-lda-in-minutes-21486f5aa925 , https://towardsdatascience.com/end-to-end-topic-modeling-in-python-latent-dirichlet-allocation-lda-35ce4ed6b3e0 , https://larevueia.fr/latent-dirichlet-allocation-topic-modeling-en-python/

In [44]:
def preprocess_text(text_list):
    '''
    Given a list of strings it performs classic text preprocessing: 
    removal of punctuation and stop-words, transformation to lowercase, lemmatization and tokenization. 
    The output is a list of lists of tokens.
    '''
    
    # Define punctuation characters
    punctuation = string.punctuation

    # Initialize lemmatizer
    lemmatizer = WordNetLemmatizer()

    preprocessed_texts = []

    for text in text_list:
        # Remove punctuation
        text = ''.join([char for char in text if char not in punctuation])

        # Convert to lowercase and remove stopwords
        text = remove_stopwords(text.lower())

        # Tokenization and lemmatization
        tokens = [lemmatizer.lemmatize(token) for token in simple_preprocess(text)]

        preprocessed_texts.append(tokens)

    return preprocessed_texts

In [24]:
preprocessed_docs = preprocess_text(docs)
print(preprocessed_docs[0:2])

[['donate', 'amazing', 'turning', 'pointinjecting', 'virus', 'genetic', 'code', 'order', 'provoke', 'immune', 'response', 'remains', 'stable', 'minus', 'month', 'kept', 'standard', 'fridge', 'month', 'showcasing', 'magic', 'genome', 'science', 'ivermectin', 'approved', 'treatment', 'viral', 'infection', 'including', 'sarscov', 'infection', 'fda', 'issued', 'warning', 'april', 'ivermectin', 'intended', 'use', 'animal', 'treat', 'covid', 'humansas', 'think', 'ivermectin', 'great', 'shot', 'working', 'question', 'data', 'gathering', 'chiapas', 'poor', 'area', 'better', 'study', 'im', 'interested', 'lack', 'reporting', 'usa', 'europe', 'debunking', 'eerie', 'silencecant', 'confirm', 'actual', 'data', 'seen', 'info', 'canada', 'showing', 'invermectin', 'silver', 'bullet', 'covidhubs', 'diagnosed', 'covid', 'early', 'december', 'took', 'hcq', 'ivermectin', 'zinc', 'vitamin', 'id', 'love', 'tell', 'experience', 'short', 'answer', 'worked', 'usi', 'believe', 'source', 'study', 'maybe', 'transl

In [50]:
# Create Dictionary
dictionary = gensim.corpora.Dictionary(preprocessed_docs)
# Remove words that appear less than x times
dictionary.filter_extremes(no_below=15, keep_n=1000)
# Dictionary size
print('Dictionary size', len(dictionary))

Dictionary size 1000


In [51]:
# Bag of words
BoW = [dictionary.doc2bow(doc) for doc in preprocessed_docs]

In [104]:
# Try LDA with different number of topics to extract
num_topics = [5, 10, 25, 50, 100, 126]
lda_models = {}
coherences = []

for n in tqdm(num_topics):
     # LDA model
     lda_model = gensim.models.LdaMulticore(BoW, num_topics = n, id2word = dictionary, random_state = 8375, passes = 25)
     lda_models[n] = lda_model


100%|██████████| 6/6 [54:25<00:00, 544.17s/it]


In [105]:
coherences = []
for n in lda_models:          
    # Evaluate the coherence of the model
     coherence_model_lda = gensim.models.CoherenceModel(model=lda_models[n], texts=preprocessed_docs, dictionary=dictionary, coherence='u_mass')
     coherence_lda = coherence_model_lda.get_coherence()
     coherences.append(coherence_lda)

# Create line chart
plt.plot(num_topics, coherences, marker='o', linestyle='-')
plt.xlabel('Number of Topics')
plt.ylabel('Coherence of the model')
plt.show()

In [102]:
coherences = []
for n in tqdm(lda_models):          
    # Evaluate the coherence of the model
     coherence_model_lda = gensim.models.CoherenceModel(model=lda_models[n], texts=preprocessed_docs, dictionary=dictionary, coherence='c_v')
     coherence_lda = coherence_model_lda.get_coherence()
     coherences.append(coherence_lda)

# Create line chart
plt.plot(num_topics, coherences, marker='o', linestyle='-')
plt.xlabel('Number of Topics')
plt.ylabel('Coherence of the model')
plt.show()

100%|██████████| 6/6 [17:12<00:00, 172.09s/it]


In [107]:
# Visualize topics
pyLDAvis.enable_notebook()
pyLDAvis.gensim_models.prepare(lda_models[10], BoW, dictionary)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.037632  0.223739       1        1  23.050220
8     -0.031711  0.129818       2        1  11.352730
6     -0.035679  0.264344       3        1  10.684818
9     -0.094181 -0.011340       4        1  10.434169
2     -0.136087 -0.152227       5        1   9.678654
3      0.100534  0.060376       6        1   9.573631
1      0.287570 -0.038703       7        1   6.990115
4     -0.192907 -0.119906       8        1   6.727708
5      0.270686 -0.160464       9        1   5.878295
7     -0.130592 -0.195635      10        1   5.629659, topic_info=           Term          Freq         Total Category  logprob  loglift
908     vaccine  75324.000000  75324.000000  Default  30.0000  30.0000
429  ivermectin  81353.000000  81353.000000  Default  29.0000  29.0000
90       bleach  36265.000000  36265.000000  Default  28.0000  28.0000
528     moderna  33667.000000  33667.000000  Default  27.0000  27.0000
887       trump  24850.000000  24850.000000  Default  26.0000  26.0000
..          ...           ...           ...      ...      ...      ...
233          dr   1481.405770  13487.789381  Topic10  -4.7283   0.6683
199       death   1446.653254  21058.757109  Topic10  -4.7520   0.1991
185        cure   1343.669913  17359.137235  Topic10  -4.8258   0.3184
551         new   1274.222381  20259.443483  Topic10  -4.8789   0.1108
247   effective   1176.258712  19273.444478  Topic10  -4.9589   0.0807

[536 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
4         1  0.803201  account
4         2  0.105407  account
4         4  0.001054  account
4         5  0.007378  account
4         6  0.075893  account
...     ...       ...      ...
968       4  0.074849    youve
968       5  0.026591    youve
971       4  0.068359     zinc
971       5  0.002464     zinc
971      10  0.929061     zinc

[2080 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 9, 7, 10, 3, 4, 2, 5, 6, 8])

In [106]:
# Visualize topics
pyLDAvis.enable_notebook()
pyLDAvis.gensim_models.prepare(lda_models[50], BoW, dictionary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
8      0.208551  0.129490       1        1  6.571347
0      0.214962  0.039187       2        1  4.637616
6      0.169468  0.107942       3        1  4.353106
2      0.070899  0.074354       4        1  4.036807
19     0.236620  0.130249       5        1  3.261815
1     -0.083328 -0.319699       6        1  3.219936
23    -0.284872  0.130524       7        1  3.087073
24    -0.156762  0.160707       8        1  3.048192
28     0.085101 -0.125014       9        1  2.660001
21     0.121803 -0.013492      10        1  2.463243
29     0.126150 -0.003626      11        1  2.413382
44     0.152611  0.130202      12        1  2.402668
5      0.027283 -0.185637      13        1  2.304706
42    -0.270257 -0.010361      14        1  2.299492
33    -0.225781  0.119217      15        1  2.088356
3      0.015417 -0.122649      16        1  2.023258
47     0.088691 -0.096487      17        1  2.021810
40    -0.186969  0.144719      18        1  2.003975
9     -0.051734 -0.253342      19        1  1.993694
4      0.015863  0.062995      20        1  1.982760
17    -0.222274  0.164128      21        1  1.807390
41    -0.037501  0.090374      22        1  1.778633
27     0.127007 -0.036685      23        1  1.770142
49     0.023138 -0.096060      24        1  1.753257
12    -0.064733  0.055749      25        1  1.683982
13     0.045407  0.001271      26        1  1.665233
38    -0.154456 -0.291940      27        1  1.659803
18    -0.158767  0.019107      28        1  1.640735
45     0.148817  0.078686      29        1  1.610732
16     0.073136  0.016642      30        1  1.579084
39    -0.138952  0.024591      31        1  1.576111
20     0.125907  0.027434      32        1  1.561021
35     0.012563  0.034363      33        1  1.521978
7     -0.126377 -0.160992      34        1  1.439230
22    -0.016055 -0.029417      35        1  1.415496
43     0.026994 -0.141760      36        1  1.365265
10    -0.122623  0.085880      37        1  1.331708
34    -0.003116 -0.099447      38        1  1.321128
14     0.095644 -0.051271      39        1  1.300750
25     0.053924 -0.012426      40        1  1.286288
36     0.079000  0.035660      41        1  1.280154
46    -0.080130  0.125069      42        1  1.261308
11    -0.027763  0.129940      43        1  1.173242
48     0.023588 -0.056174      44        1  1.129759
26     0.011790 -0.040772      45        1  1.119099
32     0.061184 -0.057472      46        1  0.954773
30     0.076839  0.091321      47        1  0.941668
37     0.000354 -0.049445      48        1  0.787767
15    -0.129440  0.044995      49        1  0.756465
31     0.023178 -0.000629      50        1  0.654562, topic_info=           Term          Freq         Total Category  logprob  loglift
908     vaccine  74929.000000  74929.000000  Default  30.0000  30.0000
429  ivermectin  75330.000000  75330.000000  Default  29.0000  29.0000
595      people  36826.000000  36826.000000  Default  28.0000  28.0000
90       bleach  33717.000000  33717.000000  Default  27.0000  27.0000
528     moderna  28987.000000  28987.000000  Default  26.0000  26.0000
..          ...           ...           ...      ...      ...      ...
329       going    108.968823   8088.594737  Topic50  -5.1861   0.7218
871        time    133.027419  13481.462186  Topic50  -4.9866   0.4104
322     getting     75.274661   5575.573509  Topic50  -5.5560   0.7240
462         let     71.735858   7146.078434  Topic50  -5.6042   0.4276
873        told     56.326617   4025.420866  Topic50  -5.8460   0.7597

[2028 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
1         1  0.105253  absolutely
1         3  0.045108  absolutely
1         4  0.170145  absolutely
1         5  0.143239  absolutely
1         8  0.072806  absolutely
...     ...       ...         ...
970      42  0.001676        zero
971  

In [108]:
# Visualize topics
pyLDAvis.enable_notebook()
pyLDAvis.gensim_models.prepare(lda_models[126], BoW, dictionary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
117   -0.143629  0.171182       1        1  2.591181
93     0.107123 -0.058767       2        1  2.058062
27     0.091120  0.067946       3        1  1.910744
8      0.173173 -0.156295       4        1  1.861407
28     0.051365  0.217187       5        1  1.759999
...         ...       ...     ...      ...       ...
95     0.101896 -0.028735     122        1  0.347530
96     0.006773  0.070671     123        1  0.343037
26    -0.034548  0.086941     124        1  0.336690
120   -0.037044 -0.062350     125        1  0.335262
123    0.057633 -0.009871     126        1  0.275233

[126 rows x 5 columns], topic_info=            Term          Freq         Total  Category  logprob  loglift
908      vaccine  76623.000000  76623.000000   Default  30.0000  30.0000
169  coronavirus  32127.000000  32127.000000   Default  29.0000  29.0000
429   ivermectin  67903.000000  67903.000000   Default  28.0000  28.0000
90        bleach  30316.000000  30316.000000   Default  27.0000  27.0000
887        trump  27974.000000  27974.000000   Default  26.0000  26.0000
..           ...           ...           ...       ...      ...      ...
335   government     52.662990   8062.828572  Topic126  -5.0469   0.8642
913        viral     36.034594   2770.366842  Topic126  -5.4263   1.5531
389        human     41.879047   5615.835790  Topic126  -5.2760   0.9967
468         like     48.980790  19083.461972  Topic126  -5.1194  -0.0698
866        think     37.483467  11354.927543  Topic126  -5.3869   0.1818

[5705 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
0         2  0.000950  able
0         3  0.019476  able
0         4  0.026126  able
0         5  0.005700  able
0         6  0.005700  able
...     ...       ...   ...
971     105  0.000120  zinc
971     108  0.000239  zinc
971     109  0.000120  zinc
971     110  0.000718  zinc
971     112  0.001795  zinc

[56569 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[118, 94, 28, 9, 29, 7, 20, 120, 24, 75, 41, 22, 66, 37, 83, 91, 81, 115, 47, 84, 110, 2, 51, 8, 71, 112, 19, 63, 60, 1, 18, 69, 68, 65, 116, 123, 70, 125, 61, 113, 122, 85, 4, 34, 5, 10, 35, 59, 100, 43, 6, 101, 11, 73, 21, 88, 44, 14, 3, 17, 48, 15, 117, 36, 12, 42, 107, 56, 54, 25, 49, 80, 23, 46, 52, 50, 86, 39, 114, 108, 55, 53, 33, 67, 30, 78, 72, 77, 105, 57, 103, 93, 102, 58, 99, 104, 74, 32, 62, 40, 98, 87, 45, 64, 26, 90, 106, 111, 79, 89, 38, 82, 95, 92, 109, 31, 16, 76, 126, 119, 13, 96, 97, 27, 121, 124])

In [110]:
lda_models[10][BoW[0]]

[(0, 0.35048506),
 (1, 0.16160393),
 (2, 0.02048776),
 (3, 0.033244338),
 (4, 0.01861571),
 (5, 0.23443006),
 (6, 0.040612243),
 (7, 0.01180307),
 (8, 0.0812976),
 (9, 0.047420267)]

In [111]:
lda_models[10].print_topics()

[(0,
  '0.024*"people" + 0.021*"like" + 0.018*"dont" + 0.017*"know" + 0.012*"im" + 0.011*"think" + 0.010*"right" + 0.009*"thing" + 0.009*"want" + 0.009*"time"'),
 (1,
  '0.182*"vaccine" + 0.092*"moderna" + 0.040*"pfizer" + 0.037*"johnson" + 0.025*"coronavirus" + 0.019*"dos" + 0.015*"million" + 0.013*"company" + 0.012*"mrna" + 0.010*"say"'),
 (2,
  '0.130*"ivermectin" + 0.036*"treatment" + 0.033*"study" + 0.024*"use" + 0.022*"trial" + 0.017*"evidence" + 0.016*"drug" + 0.013*"prophylaxis" + 0.013*"work" + 0.010*"clinical"'),
 (3,
  '0.074*"case" + 0.057*"death" + 0.057*"new" + 0.030*"day" + 0.019*"state" + 0.018*"today" + 0.017*"rate" + 0.015*"number" + 0.014*"week" + 0.012*"coronavirus"'),
 (4,
  '0.120*"ivermectin" + 0.051*"dr" + 0.034*"treatment" + 0.026*"doctor" + 0.024*"drug" + 0.016*"cure" + 0.016*"treat" + 0.015*"watch" + 0.014*"medical" + 0.013*"senate"'),
 (5,
  '0.156*"vaccine" + 0.083*"moderna" + 0.059*"effective" + 0.042*"trial" + 0.025*"coronavirus" + 0.024*"data" + 0.024*"s

## TF-IDF

### TF-IDF at Topic ID level

We group tweets by topic ID, and use TF-IDF to identify the 10 most important words in each group.  

In [5]:
# Text by topic
df_topics_text = df_tweets[['text','created_at','topics']] \
    .explode('topics').reset_index() \
    .sort_values(by=['created_at']) \
    .groupby('topics')['text'].apply(','.join).reset_index()

# Remove words starting with '@' from the text column
df_topics_text['text'] = df_topics_text['text'].str.replace(r'@\w+\s?', '', regex=True)

# List of strings
docs_topic = list(df_topics_text['text'])
docs_topic[2]

'"To see what is in front of one\'s nose needs a constant struggle." -- George Orwell,As an immunologist, I can say what you just wrote makes no sense and has been repeatedly debunked in the scientific literature.,BREAKING RESEARCH FROM CLINICAL TRIAL on HCQ + azithromycin in treatment of COVID-19. 100% of patients with COVID-19 were virologically cured after 6 DAYS of treatment. p-value <0.0001 ,Antibiotic + antimalarial against coronavirus SARS-CoV-2: Clinical Trial Hydroxychloroquine and azithromycin as a treatment of COVID-19: results of an openlabel non-randomized clinical trial,Guys. We need to talk about this Hydroxychloroquine + Azithromycin thing. It is out of hand. It all stems from this study that came out today. The study design: Comparative viral eradication on day 6 between HCQ, HCQ + Azithro, and control (not treated) COVID-19 patients.,Please don\'t take hydroxychloroquine (Plaquenil) plus Azithromycin for #COVID19 UNLESS your doctor prescribes it. Both drugs affect the

In [6]:
# Preprocess documents
preprocessed_docs_topics = preprocess_text(docs_topic)
preprocessed_docs_topics = [' '.join(doc) for doc in preprocessed_docs_topics]

In [7]:
# Use TF-IDF consiring 1-grams, 2-grams and 3-grams
tfidf_results = {1:[], 2:[], 3:[]}

for n in tqdm(tfidf_results):

    # Initialize TfidfVectorizer
    tfidf_vectorizer = TfidfVectorizer(ngram_range=(1, n),
                                        min_df=10,
                                        # max_df=max_df,
                                        max_features=2000)

    # Fit and transform the documents
    tfidf_matrix = tfidf_vectorizer.fit_transform(preprocessed_docs_topics)
    # Get feature names (n-grams)
    tfidf_feature_names = tfidf_vectorizer.get_feature_names_out()

    tfidf_results[n] = (tfidf_matrix, tfidf_feature_names)

100%|██████████| 3/3 [02:24<00:00, 48.24s/it]


In [8]:
def extract_top_ngrams(documents, tfidf_matrix, tfidf_feature_names, top = 10):
   
    top_ngrams_per_doc = []
    for doc_idx in range(len(documents)):
        # Get TF-IDF scores for the current document
        doc_scores = tfidf_matrix[doc_idx].toarray().flatten()
        
        # Sort indices by TF-IDF score in descending order
        top_indices = doc_scores.argsort()[::-1]
        
        # Get top n-grams for the current document
        top_ngrams = [tfidf_feature_names[idx] for idx in top_indices[:top]]
        
        top_ngrams_per_doc.append(top_ngrams)
    
    return top_ngrams_per_doc

We observe some topic IDs related to discussions of Harry Potter that we would like to exclude from the dataset.
More of the other topic IDs relate to COVID, vaccines, USA, Canada, and Australia politics.  

In [9]:
# Results with 3_grams
tfidf_matrix, tfidf_feature_names = tfidf_results[3]

# Get top 10 words by topic
df_topics_text['top_n_grams'] = extract_top_ngrams(documents = preprocessed_docs_topics, tfidf_matrix = tfidf_matrix, tfidf_feature_names = tfidf_feature_names, top = 10)

# See all topics and their words
print(df_topics_text[['topics', 'top_n_grams']].to_string())

     topics                                                                                                                                    top_n_grams
0    2001p1                                         [covid, azithromycin, percentile, thread, patient, algorithmic, mute thread, tweet, mute, coronavirus]
1    2002p1                                                [covid, azithromycin, percentile, patient, thread, zinc, algorithmic, mute thread, tweet, mute]
2    2002p2                                            [covid, ivermectin, azithromycin, zinc, treatment, hcq, vaccine, patient, early, zinc azithromycin]
3    2003p1                                                            [covid, day, azithromycin, mg, corona, coronavirus, patient, treatment, home, said]
4    2003p2                                                          [covid, vaccine, ivermectin, trial, phase, people, covid vaccine, patient, india, uk]
5    2004p1                                                           

In [175]:
# Dimensionality reduction using PCA
pca = PCA(n_components=2)
tfidf_matrix_pca = pca.fit_transform(tfidf_matrix.toarray())

In [10]:
# Dimensionality reduction using UMAP
umap_model = umap.UMAP(n_components=2)
umap_embeddings = umap_model.fit_transform(tfidf_matrix)

In [183]:
# Dimensionality reduction using t-SNE
tsne_model = TSNE(n_components=2, random_state=42)
tsne_embeddings = tsne_model.fit_transform(tfidf_matrix.toarray())

In [186]:
# Create DataFrame for Plotly
data = {
    # 'Component 1': tfidf_matrix_pca[:, 0],
    'Component 1': umap_embeddings[:, 0],
    # 'Component 1': tsne_embeddings[:, 0],
    # 'Component 2': tfidf_matrix_pca[:, 1],
    'Component 2': umap_embeddings[:, 1],
    # 'Component 2': tsne_embeddings[:, 1],
    'Top n-grams': [' '.join(i) for i in df_topics_text['top_n_grams']],
    'Topic id': df_topics_text['topics']
}
df_plot = pd.DataFrame(data)

# Plot interactive scatter plot
fig = px.scatter(df_plot, x='Component 1', y='Component 2', 
                #  text='Topic id', 
                #  title='Documents Visualization in 2D (UMAP)',
                 hover_name='Topic id', hover_data= {'Component 1':False, 'Component 2': False, 'Top n-grams': True, 'Topic id': False}, 
                 width=800, height=600)
fig.update_traces(marker={'size': 20})
fig.show()

### TF-IDF at component level

In [25]:
preprocessed_docs_ = [' '.join(doc) for doc in preprocessed_docs]

# Initialize TfidfVectorizer
tfidf_vectorizer_comp = TfidfVectorizer(ngram_range=(1, 2),
                                    min_df=10,
                                    max_features=3000)

# Fit and transform the documents
tfidf_matrix_comp = tfidf_vectorizer_comp.fit_transform(preprocessed_docs_)
# Get feature names (n-grams)
tfidf_feature_names_comp = tfidf_vectorizer_comp.get_feature_names_out()

In [52]:
# Get top 10 words by topic
df_components_text['top_n_grams'] = extract_top_ngrams(documents = preprocessed_docs_, tfidf_matrix = tfidf_matrix_comp, tfidf_feature_names = tfidf_feature_names_comp, top = 15)


In [53]:
# Look at the set of words that characterize the components
list_top_n_grams = list(df_components_text['top_n_grams'])
set_top_n_grams = sorted(set(list(itertools.chain(*list_top_n_grams ))))
for i in set_top_n_grams:
    print(i)

ab
ability
able
absolute
absolutely
abuse
accept
accepted
access
according
account
accurate
accused
ace
act
acting
action
active
active case
activity
actual
actually
acute
ad
add
add new
added
adding
addition
additional
address
adm
admin
administered
administration
admission
admit
admitted
adult
advance
advanced
advantage
adverse
advice
advise
advised
adviser
advisory
advocate
advocating
affect
affected
afraid
africa
african
age
aged
agency
agenda
agent
ago
agree
agreed
agreement
ahead
aid
aint
air
air spray
airborne
aka
al
alberta
alcohol
alert
alive
alliance
allow
allowed
allowing
allows
alternative
am
amazing
america
american
american died
american people
amid
analysis
ancient
and
andor
andrew
animal
announce
announced
announcement
announces
answer
anthony
anthony fauci
anti
antibiotic
antibiotic azithromycin
antibody
antiparasitic
antiparasitic drug
antiviral
anybody
anymore
apart
app
apparently
appear
appears
application
apply
appointment
appreciate
approach
appropriate
approval
a

### Filtering components

In [78]:
words_for_filtering = ['harry', 'potter', 'harry potter', 'muggle', 'wizard']

# Identify components to exclude 
components_to_exclude = list(df_components_text[df_components_text['top_n_grams'].apply(lambda x: any(word in x for word in words_for_filtering))]['component_id'])
print('Components to exclude according to TF-IDF by component', len(components_to_exclude))
print('Tweets to exclude according to TF-IDF by component', len(df_tweets[df_tweets['component_id'].isin(components_to_exclude)]))

# Identify topics IDs related to Harry Potter
topics_to_exclude = list(df_topics_text[df_topics_text['top_n_grams'].apply(lambda x: any(word in x for word in words_for_filtering))]['topics'])
print('\n')
print('Topics to exclude', topics_to_exclude)

# Identify components to exclude based on their topics 
df_components_topics = df_tweets[['component_id', 'topics']].explode('topics')
components_to_exclude_given_topic = list(df_components_topics[df_components_topics['topics'].isin(topics_to_exclude)].groupby('component_id').size())
print('Components to exclude according to TF-IDF by topic', len(components_to_exclude_given_topic))
print('Tweets to exclude according to TF-IDF by topic', len(df_tweets[df_tweets['component_id'].isin(components_to_exclude_given_topic)]))

# Total components to exclude
union_components_to_exclude = set.union(set(components_to_exclude), set(components_to_exclude_given_topic))
print('\n')
print('Total components to exclude', len(union_components_to_exclude))
print('Total tweets to exclude', len(df_tweets[df_tweets['component_id'].isin(union_components_to_exclude)]))

Components to exclude [87, 90, 93, 94, 98, 107, 109, 116, 117, 123, 134, 145, 157, 162, 167, 174, 175, 178, 179, 180, 181, 185, 189, 190, 191, 203, 209, 213, 221, 225, 228, 229, 235, 236, 242, 243, 251, 252, 255, 263, 264, 266, 272, 273, 275, 276, 277, 278, 286, 287, 296, 298, 299, 304, 310, 311, 312, 321, 328, 330, 332, 341, 346, 371, 372, 386, 397, 401, 411, 420, 422, 431, 432, 433, 443, 458, 459, 476, 477, 494, 528, 545, 546, 573, 574, 575, 623, 624, 625, 626, 629, 651, 652, 656, 658, 679, 680, 686, 715, 719, 722, 741, 742, 744, 747, 750, 795, 806, 844, 846, 847, 850, 889, 890, 892, 897, 900, 901, 938, 945, 946, 988, 992, 995, 996, 1066, 1068, 1077, 1131, 1202, 1213, 1288, 1325, 1395, 1397, 1406, 1413, 1518, 1524, 1525, 1532, 1533, 1541, 1643, 1644, 1654, 1683, 1799, 1811, 1950, 1958, 1961, 1965, 1967, 1968, 1993, 2157, 2172, 2173, 2431, 2433, 2437, 2439, 2442, 2444, 2453, 2481, 2519, 2814, 2835, 2883, 3253, 3682, 3690, 3708, 3720, 3740, 3742, 3756, 3764, 4317, 4785, 5085, 5269, 542

In [68]:
venn2([set(components_to_exclude), set(components_to_exclude_given_topic)], set_labels = ('Components to exclude \n according to TF-IDF by component', 'Components to exclude \n according to TF-IDF by topic'))
plt.show()

In [82]:
# Save list of new_ids that should be excluded
tweets_to_exclude_given_topic = list(df_tweets[df_tweets['component_id'].isin(union_components_to_exclude)]['new_id'])
pickle.dump(tweets_to_exclude_given_topic, open("results/tweets_to_exclude_given_topic.pkl", "wb"))